The library jaakko
====

I was thinking about APL, Codd's relational model, modal logic, and Pandas,
and I designed a little library called jaakko.

In [1]:
import jaakko

Let's consider a quantity whose value is 5 in the possible world where x is 3 and y is 4.  Such conditional
quantities are called "columns", by analogy to database table columns.

In [11]:
r = jaakko.Column(('x', 'y'), {(3, 4): 5})
r

You can add new values to a column; perhaps we want $r$ to take the value 10 when $x = 6 \wedge y = 8$.

In [12]:
r.append((6, 8), 10)
r

You can do the usual arithmetic operations on column values.

In [7]:
r * r

In [9]:
r + 2

You can also compute aggregate functions.  For this purpose, let's look at a different column, one from Codd's
paper from 01971: the quantity $q$ requested of part number $p$ from supplier $s$ by project $pj$.

In [14]:
q = jaakko.Column(('s', 'p', 'pj'), {
    (1, 2, 5): 17,
    (1, 3, 5): 23,
    (2, 3, 7): 9,
    (2, 7, 5): 4,
    (4, 1, 1): 12,
})
q

We might want to know, for example, the total number of parts required by each project.  This requires
summing $q$ across values of $s$ and $p$.  Note that this is the opposite of how we formulate the problem
in SQL.

In [15]:
q.aggregate(('s', 'p'), sum)

More plausibly, we'd like to know the total cost of the parts required by each project.  Perhaps the price
depends on both the supplier and the part number.

In [26]:
price = jaakko.Column(('s', 'p'), {
    (1, 2): 1.99,
    (1, 3): 2.79,
    (2, 3): 3.09,
    (2, 7): 8.99,
    (4, 1): 0.49,
})
price

We can simply multiply the two columns, even though they have different keys;
the relevant subset of the key is used.

In [27]:
q * price

And from there we can easily calculate the totals as before.

In [29]:
def materials_budget():
    return (q * price).aggregate(('s', 'p'), sum)

materials_budget()

But suppose — not so implausibly — that projects require different numbers of parts in different years.

In [34]:
q = jaakko.Column(('s', 'p', 'pj', 'year'), {
    (1, 2, 5, 2025): 17,
    (1, 3, 5, 2025): 23,
    (2, 3, 7, 2025): 9,
    (2, 7, 5, 2025): 4,
    (4, 1, 1, 2025): 12,
    (1, 2, 5, 2026): 15,
    (1, 3, 5, 2026): 30,
    (2, 3, 7, 2026): 10,
    (2, 7, 5, 2026): 16,
    (4, 1, 1, 2026): 6,
})
q

This new dependency implicitly flows through our existing code:

In [35]:
materials_budget()